$\partial_t c+\nabla\cdot(cu-k\nabla c)=f$

In [15]:
import netgen.gui
from ngsolve import *
from netgen.geom2d import SplineGeometry
from math import pi
from netgen.geom2d import unit_square
#  (0,1)        Gamma_S         (1,1)
#        +----------------------+
#        |     Subdomain 1      |
#Gamma_S |                      | Gamma_S
#        |        Gamma_I       |
#(0,0.5) +----------------------+ (1,0.5)
#        |                      |
#Gamma_D |                      | Gamma_D
#        |   Subdomain 2        |
#        +----------------------+
#  (0,0)      Gamma_D           (1,0)
geo = SplineGeometry()
points     = [ (0, 0), (1, 0),  (1, 0.5), (1, 1), (0, 1), (0, 0.5)]
pnums    = [geo.AppendPoint(*pt) for pt in points]
# Make a list of line segments
l1 = geo.Append(["line", 0, 1], leftdomain=2, rightdomain=0, bc="GammaD")
l2 = geo.Append(["line", 1, 2], leftdomain=2, rightdomain=0, bc="GammaD")
l3 = geo.Append(["line", 2, 3], leftdomain=1, rightdomain=0, bc="GammaS")
l4 = geo.Append(["line", 3, 4], leftdomain=1, rightdomain=0, bc="GammaS")
l5 = geo.Append(["line", 4, 5], leftdomain=1, rightdomain=0, bc="GammaS")
l6 = geo.Append(["line", 5, 0], leftdomain=2, rightdomain=0, bc="GammaD")
l7 = geo.Append(["line", 5, 2], leftdomain=1, rightdomain=2, bc="GammaI")

geo.SetMaterial(1, "stokesregion")
geo.SetMaterial(2, "darcyregion")

#mesh = Mesh(unit_square.GenerateMesh(maxh=0.5) )
mesh = Mesh(geo.GenerateMesh(maxh=0.5))

Tend = 1 # End time
t = Parameter(0.0)
kk=1

# c exact
cexact = CoefficientFunction(sin(2*pi*(x-t))*cos(2*pi*(y-t)))
cinit  = CoefficientFunction(sin(2*pi*(x))*cos(2*pi*(y)))
# gradient of c
c_dx =  2*pi*cos(2*pi*(x-t))*cos(2*pi*(y-t))
c_dy =  -2*pi*sin(2*pi*(x-t))*sin(2*pi*(y-t))
c_dt =  2*pi*sin(2*pi*(x-t))*sin(2*pi*(y-t))- 2*pi*cos(2*pi*(x-t))*cos(2*pi*(y-t))
grad_cexact = CoefficientFunction((c_dx, c_dy))

u   = CoefficientFunction((1, 2))

cu  = cexact*u
dif = cu - kk*grad_cexact
div = dif[0].Diff(x) + dif[1].Diff(y)

#source f
source= CoefficientFunction(c_dt + div)

l=2

C    = L2(mesh, order=l)
Cbar = FacetFESpace(mesh, order=l) 
X    = FESpace([C, Cbar])

c, cbar = X.TrialFunction()
w, wbar = X.TestFunction()

# Penalty parameter
beta_c = 6*l**2
#beta_f = 10*k**2
n = specialcf.normal(mesh.dim)
h = specialcf.mesh_size
gi= CoefficientFunction((-cu+kk*grad_cexact)*n)
go= CoefficientFunction(kk*grad_cexact*n)
g = IfPos(u*n,go,gi)    
# Bilinear Form
a = BilinearForm(X)
    
B_dx = -(c*u)*grad(w)+kk*grad(c)*grad(w)
B_ds = (-u*c + kk*grad(c)-(IfPos(u*n,0,1)*u-(beta_c*kk)/h*n)*(cbar-c))*n*(wbar-w)\
           - (kk*grad(w))*n*(c-cbar)
B_ds_out = (u*n)*wbar*cbar
a += B_dx * dx
a += B_ds * dx(element_boundary=True)
#a += IfPos(u*n,1,0)*B_ds_out*ds(skeleton=True,definedon=mesh.Boundaries("right|top|left|bottom"))
a += IfPos(u*n,1,0)*B_ds_out*ds(skeleton=True,definedon=mesh.Boundaries("GammaS|GammaD"))

a.Assemble()    

# Mstar = M + theta*dt*A
m = BilinearForm(X)
m += c*w*dx
m.Assemble()
# Linear forms
f = LinearForm(X)  
f += source*w*dx
f += g*wbar*ds(skeleton=True)
gfu = GridFunction(X)

#initial

dt=0.01
output = []
def Solve_transport(dt):
    X.Update()
    gfu.Update()
	    
    #Linear forms
    a.Assemble()
    m.Assemble()
    f.Assemble()
               
    mstar = m.mat.CreateMatrix()
    mstar.AsVector().data = m.mat.AsVector() +  dt * a.mat.AsVector()
    invmstar = mstar.Inverse(freedofs=X.FreeDofs())
    gfu.components[0].Set(cinit)
    res = gfu.vec.CreateVector()

    for it in range(1,int(Tend/dt + 1)+1):
        t.Set(it*dt)
        f.Assemble()

        res.data = dt * f.vec - dt * a.mat * gfu.vec 

        gfu.vec.data += invmstar * res

        #Redraw(blocking=True)
    u=gfu.components[0]
    err = sqrt(Integrate((u-cexact)**2, mesh))
    print("\n error c:", err)
    #Draw(gfu.components[0],mesh,"c")
    output.append ((X.ndof, err))
    print(output)


while X.ndof < 10000:
    mesh.Refine()
    Solve_transport(dt)
    dt=dt/4
con = gfu.components[0]
Draw(con,mesh,"c")
# table of convergence
i = 1
while i < len(output):
    order = log(output[i-1][1]/output[i][1])/log(2)
 
    print("%0.3f | %0.3e " %
      (order, output[i-1][1]))
    i =  i+1



 error c: 0.14426949198311745
[(376, 0.14426949198311745)]

 error c: 0.4160443316705295
[(376, 0.14426949198311745), (1464, 0.4160443316705295)]

 error c: 0.4315021928639826
[(376, 0.14426949198311745), (1464, 0.4160443316705295), (5752, 0.4315021928639826)]

 error c: 0.38413356577616375
[(376, 0.14426949198311745), (1464, 0.4160443316705295), (5752, 0.4315021928639826), (22776, 0.38413356577616375)]
-1.528 | 1.443e-01 
-0.053 | 4.160e-01 
0.168 | 4.315e-01 


In [ ]:
#unit square
[(289, 0.010284618987461453), (1113, 0.004995344740301261), (4345, 0.0006983296412464655), (17145, 0.00011042835139796657), (68089, 2.163531382003384e-05)]
1.042 | 1.028e-02 
2.839 | 4.995e-03 
2.661 | 6.983e-04 
2.352 | 1.104e-04